# Cours 3 : Machine Learning - Algorithmes supervisés (1/2)

## Préambule

Les objectifs de cette séance (3h) sont :
* Préparation des bases de modélisation (sampling)
* Mettre en application un modèle supervisé simple.
* Construire un modèle de Machine Learning (cross-validation et hyperparamétrage) pour résoudre un problème de régression
* Analyser les performances du modèle

## Préparation du workspace

### Import de librairies 

In [1]:
# Données
import numpy as np
import pandas as pd

# Graphiques
import seaborn as sns

sns.set()
import plotly.express as px
import sklearn.metrics as metrics
import sklearn.preprocessing as preproc

# Statistiques
from scipy.stats import chi2_contingency

# Machine Learning
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold, cross_val_score, train_test_split
from sklearn.tree import DecisionTreeRegressor

### Définition des fonctions 

In [2]:
def cramers_V(var1, var2):
    crosstab = np.array(
        pd.crosstab(var1, var2, rownames=None, colnames=None)
    )  # Cross table building
    stat = chi2_contingency(crosstab)[
        0
    ]  # Keeping of the test statistic of the Chi2 test
    obs = np.sum(crosstab)  # Number of observations
    mini = (
        min(crosstab.shape) - 1
    )  # Take the minimum value between the columns and the rows of the cross table
    return stat / (obs * mini)

### Constantes

In [3]:
input_path = "./1_inputs"
output_path = "./2_outputs"

### Import des données

In [4]:
path = input_path + "/base_retraitee.csv"
data_retraitee = pd.read_csv(path, sep=",", decimal=".")

## Algorithme supervisé : CART 

Dans cette partie l'objectif est de construire un modèle simple (algorithme CART) afin de voir les différentes étapes nécessaire au lancement d'un modèle
Nous modéliserons directement le coût des sinistres. 

### Construction du modèle

La première étape est de calculer les côut moyen de chaque sinistre (target ou variable réponse). Cette variable sera la variable à prédire en fonction des variables explicatives.

In [5]:
data_model = data_retraitee

# Filtre pour ne garder que les lignes qui ont un sinistre (NB > 0)
data_model = data_model[data_model["NB"] > 0]

# Calcul du cout moyen "théorique" des sinistres
data_model["CM"] = data_model["CHARGE"] / data_model["NB"]
data_model = data_model.drop(["CHARGE", "NB", "EXPO"], axis=1)
data_model.head()

/var/folders/tp/_ld5_pzs6nx6mv1pbjhq1l740000gn/T/ipykernel_79947/358057511.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_model["CM"] = data_model["CHARGE"] / data_model["NB"]


ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION      GROUPE_KM  \
10       2019              (0,1]                       MENSUEL      [0;20000[   
34       2020             (-1,0]                       MENSUEL  [20000;40000[   
36       2019             (-1,0]                       MENSUEL  [20000;40000[   
78       2019             (-1,0]                       MENSUEL  [20000;40000[   
89       2018              (1,2]                       MENSUEL  [20000;40000[   

   ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE  DEUXIEME_CONDUCTEUR  \
10           C                    40     M                False   
34           C                    27     M                 True   
36           L                    19     M                False   
78           B                    40     M                False   
89           C                    20     M                False   

    ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE EQUIPEMENT_SECURITE  \
10                 37              2017.0  ESSENCE                VRAI   
34                 13              2018.0    AUTRE                FAUX   
36                  2              2017.0  ESSENCE                VRAI   
78                 45              2018.0   DIESEL                FAUX   
89                 11              2014.0  ESSENCE                FAUX   

   VALEUR_DU_BIEN       CM  
10  [15000;20000[  1072.98  
34  [35000;99999[  3750.00  
36      [0;10000[  1838.49  
78  [15000;20000[  4892.74  
89  [25000;35000[   166.73

**Exercice :** construisez les statistiques descriptives de la base utilisée.

In [6]:
data_model.describe(include="all")

ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION  \
count    824.000000                824                           824   
unique          NaN                  5                             3   
top             NaN              (0,1]                       MENSUEL   
freq            NaN                297                           398   
mean    2018.384709                NaN                           NaN   
std        1.515833                NaN                           NaN   
min     2016.000000                NaN                           NaN   
25%     2017.000000                NaN                           NaN   
50%     2018.000000                NaN                           NaN   
75%     2020.000000                NaN                           NaN   
max     2021.000000                NaN                           NaN   

        GROUPE_KM ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE DEUXIEME_CONDUCTEUR  \
count         824         824            824.000000   824                 824   
unique          4          14                   NaN     2                   2   
top     [0;20000[           C                   NaN     M               False   
freq          391         269                   NaN   483                 663   
mean          NaN         NaN             44.383495   NaN                 NaN   
std           NaN         NaN             13.808217   NaN                 NaN   
min           NaN         NaN             19.000000   NaN                 NaN   
25%           NaN         NaN             34.000000   NaN                 NaN   
50%           NaN         NaN             43.000000   NaN                 NaN   
75%           NaN         NaN             53.000000   NaN                 NaN   
max           NaN         NaN             94.000000   NaN                 NaN   

        ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE EQUIPEMENT_SECURITE  \
count          824.000000          824.000000      824                 824   
unique                NaN                 NaN        3                   2   
top                   NaN                 NaN  ESSENCE                FAUX   
freq                  NaN                 NaN      413                 517   
mean            35.688107         2015.212379      NaN                 NaN   
std             19.370621            3.163782      NaN                 NaN   
min              1.000000         1998.000000      NaN                 NaN   
25%             18.000000         2014.000000      NaN                 NaN   
50%             35.000000         2016.000000      NaN                 NaN   
75%             53.000000         2017.000000      NaN                 NaN   
max             70.000000         2021.000000      NaN                 NaN   

       VALEUR_DU_BIEN            CM  
count             824    824.000000  
unique              6           NaN  
top     [10000;15000[           NaN  
freq              213           NaN  
mean              NaN   4246.016978  
std               NaN   6869.616917  
min               NaN      7.500000  
25%               NaN   1159.961250  
50%               NaN   2541.650000  
75%               NaN   4193.797500  
max               NaN  83421.850000

In [7]:
# Observation de la distribution
fig = px.histogram(data_model, x="CM")
fig.show()

#### Etude des corrélations parmi les variables explicatives

**Question :** Selon vous, pourquoi faut-il s'intéresser à la corrélation des variables ? 

*Réponse*: Pour avoir un modèle qui fit mieux + déterminer un potentiel effet de causalité entre features et target + sélectionner certaines variables.

In [8]:
data_set = data_model.drop("CM", axis=1)
data_set.shape

(824, 13)

In [9]:
# Séparation en variables qualitatives ou catégorielles
variables_na = []
variables_numeriques = []
variables_01 = []
variables_categorielles = []
for colu in data_set.columns:
    if True in data_set[colu].isna().unique():
        variables_na.append(data_set[colu])
    else:
        if str(data_set[colu].dtypes) in ["int32", "int64", "float64"]:
            if len(data_set[colu].unique()) == 2:
                variables_categorielles.append(data_set[colu])
            else:
                variables_numeriques.append(data_set[colu])
        else:
            if len(data_set[colu].unique()) == 2:
                variables_categorielles.append(data_set[colu])
            else:
                variables_categorielles.append(data_set[colu])

##### Corrélation des variables catégorielles :

In [10]:
vars_categorielles = pd.DataFrame(variables_categorielles).transpose()

In [11]:
# Test du V de Cramer
rows = []

for var1 in vars_categorielles:
    col = []
    for var2 in vars_categorielles:
        cramers = cramers_V(
            vars_categorielles[var1], vars_categorielles[var2]
        )  # V de Cramer
        col.append(round(cramers, 2))  # arrondi du résultat
    rows.append(col)

cramers_results = np.array(rows)
v_cramer_resultats = pd.DataFrame(
    cramers_results,
    columns=vars_categorielles.columns,
    index=vars_categorielles.columns,
)

v_cramer_resultats

CONTRAT_ANCIENNETE  \
CONTRAT_ANCIENNETE                           1.00   
FREQUENCE_PAIEMENT_COTISATION                0.00   
GROUPE_KM                                    0.01   
ZONE_RISQUE                                  0.02   
GENRE                                        0.01   
DEUXIEME_CONDUCTEUR                          0.01   
ENERGIE                                      0.01   
EQUIPEMENT_SECURITE                          0.00   
VALEUR_DU_BIEN                               0.01   

                               FREQUENCE_PAIEMENT_COTISATION  GROUPE_KM  \
CONTRAT_ANCIENNETE                                      0.00       0.01   
FREQUENCE_PAIEMENT_COTISATION                           1.00       0.00   
GROUPE_KM                                               0.00       1.00   
ZONE_RISQUE                                             0.01       0.04   
GENRE                                                   0.01       0.01   
DEUXIEME_CONDUCTEUR                                     0.00       0.00   
ENERGIE                                                 0.00       0.04   
EQUIPEMENT_SECURITE                                     0.01       0.01   
VALEUR_DU_BIEN                                          0.03       0.04   

                               ZONE_RISQUE  GENRE  DEUXIEME_CONDUCTEUR  \
CONTRAT_ANCIENNETE                    0.02   0.01                 0.01   
FREQUENCE_PAIEMENT_COTISATION         0.01   0.01                 0.00   
GROUPE_KM                             0.04   0.01                 0.00   
ZONE_RISQUE                           1.00   0.01                 0.02   
GENRE                                 0.01   1.00                 0.00   
DEUXIEME_CONDUCTEUR                   0.02   0.00                 0.99   
ENERGIE                               0.03   0.03                 0.00   
EQUIPEMENT_SECURITE                   0.04   0.01                 0.00   
VALEUR_DU_BIEN                        0.02   0.08                 0.02   

                               ENERGIE  EQUIPEMENT_SECURITE  VALEUR_DU_BIEN  
CONTRAT_ANCIENNETE                0.01                 0.00            0.01  
FREQUENCE_PAIEMENT_COTISATION     0.00                 0.01            0.03  
GROUPE_KM                         0.04                 0.01            0.04  
ZONE_RISQUE                       0.03                 0.04            0.02  
GENRE                             0.03                 0.01            0.08  
DEUXIEME_CONDUCTEUR               0.00                 0.00            0.02  
ENERGIE                           1.00                 0.02            0.08  
EQUIPEMENT_SECURITE               0.02                 0.99            0.05  
VALEUR_DU_BIEN                    0.08                 0.05            1.00

In [44]:
# On repère les variables trop corrélées
for i in range(v_cramer_resultats.shape[0]):
    for j in range(i + 1, v_cramer_resultats.shape[0]):
        if v_cramer_resultats.iloc[i, j] > 0.7:
            print(
                v_cramer_resultats.index.to_numpy()[i]
                + " et "
                + v_cramer_resultats.columns[j]
                + " sont trop dépendantes, V-CRAMER = "
                + str(v_cramer_resultats.iloc[i, j])
            )

##### Corrélation des variables numériques :

In [13]:
vars_numeriques = pd.DataFrame(variables_numeriques).transpose()

In [14]:
# Corrélation de Pearson
correlations_num = vars_numeriques.corr(method="pearson")
correlations_num

ANNEE_CTR  AGE_ASSURE_PRINCIPAL  ANCIENNETE_PERMIS  \
ANNEE_CTR              1.000000              0.026613           0.040797   
AGE_ASSURE_PRINCIPAL   0.026613              1.000000           0.540899   
ANCIENNETE_PERMIS      0.040797              0.540899           1.000000   
ANNEE_CONSTRUCTION     0.387562             -0.031655           0.033320   

                      ANNEE_CONSTRUCTION  
ANNEE_CTR                       0.387562  
AGE_ASSURE_PRINCIPAL           -0.031655  
ANCIENNETE_PERMIS               0.033320  
ANNEE_CONSTRUCTION              1.000000

In [15]:
# On repère les variables trop corrélées
nb_variables = correlations_num.shape[0]
for i in range(nb_variables):
    for j in range(i + 1, nb_variables):
        if abs(correlations_num.iloc[i, j]) > 0.7:
            print(
                correlations_num.index.to_numpy()[i]
                + " et "
                + correlations_num.columns[j]
                + " sont trop dépendantes, corr = "
                + str(correlations_num.iloc[i, j])
            )

**Question :** quels sont vos commentaires ?

*Réponse*: Aucune des variables ne semblent corrélées.

#### Preprocessing

Deux étapes sont nécessaires avant de lancer l'apprentissage d'un modèle, c'est ce qu'on connait comme le *Preprocessing* :

* Les modèles proposés par la librairie "sklearn" ne gèrent que des variables numériques. Il est donc nécessaire de transformer les variables catégorielles en variables numériques : ce processus s'appelle le *One Hot Encoding*.
* Normaliser les données numériques

**Exercice :** proposez un bout de code permettant de réaliser le One Hot Encoding des variables catégorielles. Vous pourrez utiliser la fonction "preproc.OneHotEncoder" de la librairie sklearn

In [16]:
# One hot encoding des variables catégorielles
preproc_ohe = preproc.OneHotEncoder(handle_unknown="ignore")
preproc_ohe = preproc.OneHotEncoder(drop="first", sparse_output=False).fit(
    vars_categorielles
)

variables_categorielles_ohe = preproc_ohe.transform(vars_categorielles)
variables_categorielles_ohe = pd.DataFrame(
    variables_categorielles_ohe,
    columns=preproc_ohe.get_feature_names_out(vars_categorielles.columns),
)
variables_categorielles_ohe.head()

CONTRAT_ANCIENNETE_(0,1]  CONTRAT_ANCIENNETE_(1,2]  \
0                       1.0                       0.0   
1                       0.0                       0.0   
2                       0.0                       0.0   
3                       0.0                       0.0   
4                       0.0                       1.0   

   CONTRAT_ANCIENNETE_(2,5]  CONTRAT_ANCIENNETE_(5,10]  \
0                       0.0                        0.0   
1                       0.0                        0.0   
2                       0.0                        0.0   
3                       0.0                        0.0   
4                       0.0                        0.0   

   FREQUENCE_PAIEMENT_COTISATION_MENSUEL  \
0                                    1.0   
1                                    1.0   
2                                    1.0   
3                                    1.0   
4                                    1.0   

   FREQUENCE_PAIEMENT_COTISATION_TRIMESTRIEL  GROUPE_KM_[20000;40000[  \
0                                        0.0                      0.0   
1                                        0.0                      1.0   
2                                        0.0                      1.0   
3                                        0.0                      1.0   
4                                        0.0                      1.0   

   GROUPE_KM_[40000;60000[  GROUPE_KM_[60000;99999[  ZONE_RISQUE_B  ...  \
0                      0.0                      0.0            0.0  ...   
1                      0.0                      0.0            0.0  ...   
2                      0.0                      0.0            0.0  ...   
3                      0.0                      0.0            1.0  ...   
4                      0.0                      0.0            0.0  ...   

   GENRE_M  DEUXIEME_CONDUCTEUR_True  ENERGIE_DIESEL  ENERGIE_ESSENCE  \
0      1.0                       0.0             0.0              1.0   
1      1.0                       1.0             0.0              0.0   
2      1.0                       0.0             0.0              1.0   
3      1.0                       0.0             1.0              0.0   
4      1.0                       0.0             0.0              1.0   

   EQUIPEMENT_SECURITE_VRAI  VALEUR_DU_BIEN_[10000;15000[  \
0                       1.0                           0.0   
1                       0.0                           0.0   
2                       1.0                           0.0   
3                       0.0                           0.0   
4                       0.0                           0.0   

   VALEUR_DU_BIEN_[15000;20000[  VALEUR_DU_BIEN_[20000;25000[  \
0                           1.0                           0.0   
1                           0.0                           0.0   
2                           0.0                           0.0   
3                           1.0                           0.0   
4                           0.0                           0.0   

   VALEUR_DU_BIEN_[25000;35000[  VALEUR_DU_BIEN_[35000;99999[  
0                           0.0                           0.0  
1                           0.0                           1.0  
2                           0.0                           0.0  
3                           0.0                           0.0  
4                           1.0                           0.0  

[5 rows x 32 columns]

**Exercice :** proposez un bout de code permettant normaliser les variables numériques présentes dans la base. Vous pourrez utiliser la fonction "preproc.StandardScaler" de la librairie sklearn

In [17]:
# Normalisation des varibales numériques
preproc_scale = preproc.StandardScaler(with_mean=True, with_std=True)
preproc_scale.fit(vars_numeriques)

vars_numeriques_scaled = preproc_scale.transform(vars_numeriques)
vars_numeriques_scaled = pd.DataFrame(
    vars_numeriques_scaled, columns=vars_numeriques.columns
)
vars_numeriques_scaled.head()

ANNEE_CTR  AGE_ASSURE_PRINCIPAL  ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION
0   0.406156             -0.317648           0.067767            0.565370
1   1.066260             -1.259689          -1.171975            0.881639
2   0.406156             -1.839406          -1.740190            0.565370
3   0.406156             -0.317648           0.481014            0.881639
4  -0.253948             -1.766941          -1.275287           -0.383438

#### Sampling

**Exercice :** proposez un bout de code permettant construire la base d'apprentissage (80% des données) et la base de test (20%).

In [18]:
X_global = vars_numeriques_scaled.merge(
    variables_categorielles_ohe, left_index=True, right_index=True
)

In [19]:
# Réorganisation des données
X = X_global.to_numpy()
Y = data_model["CM"]

# Sampling en 80% train et 20% test
X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42
)

#### Fitting

**Exercice :** proposez un bout de code permettant construire le modèle

In [20]:
# Initialisation de l'objet
model_CART = DecisionTreeRegressor()

# Train Decision Tree Classifer
model_CART = model_CART.fit(X_train, y_train)

**Exercice :** proposez un bout de code permettant d'évaluer les performances du modèle (MAE, MSE et RMSE)

In [21]:
# Prédictions sur l'ensemble d'entraînement
y_pred_train = model_CART.predict(X_train)

mae = metrics.mean_absolute_error(y_train, y_pred_train)
mse = metrics.mean_squared_error(y_train, y_pred_train)
rmse = metrics.root_mean_squared_error(y_train, y_pred_train)

print(f"MAE: {mae:.2f}")
print(f"MSE: {mse:.2f}")
print(f"RMSE: {rmse:.2f}")

MAE: 0.00
MSE: 0.00
RMSE: 0.00


In [22]:
y_pred_test = model_CART.predict(X_test)

mae = metrics.mean_absolute_error(y_test, y_pred_test)
mse = metrics.mean_squared_error(y_test, y_pred_test)
rmse = metrics.root_mean_squared_error(y_test, y_pred_test)

print(f"MAE: {mae:.2f}")
print(f"MSE: {mse:.2f}")
print(f"RMSE: {rmse:.2f}")

MAE: 5047.78
MSE: 88252585.29
RMSE: 9394.28


**Question :** que pensez-vous des performances de ce modèle ?

*Réponse*: 

Erreur Absolue Moyenne (MAE)
La MAE représente l'écart absolu moyen entre les prédictions du modèle et les valeurs réelles. Une MAE de 5950.05 signifie qu'en moyenne, notre modèle commet une erreur de cette magnitude, dans l'unité de la variable cible. C'est l'indicateur le plus direct de l'erreur de prédiction moyenne.

Racine de l'Erreur Quadratique Moyenne (RMSE)
La RMSE est la racine carrée de la moyenne des erreurs au carré ($RMSE = \sqrt{MSE}$). En raison de l'opération de mise au carré, cette métrique est particulièrement sensible aux grandes erreurs. La valeur obtenue est de 12651.79.

## Algorithme supervisé : Random Forest  

A ce stade, nous avons vu les différentes étapes pour lancer un algorithme de Machine Learning. Néanmoins, ces étapes ne sont pas suffisantes pour construire un modèle performant.  
En effet, afin de construire un modèle performant le Data Scientist doit agir sur l'apprentissage du modèle. Dans ce qui suit nous :
* Changerons d'algorithme pour utiliser un algorithme plus performant (Random Forest)
* Raliserons un *grid search* sur les paramètres du modèle
* Appliquerons l'apprentissage par validation croisée


### Modèle avec Validation Croisée

#### Sampling

In [23]:
X_global = vars_numeriques_scaled.merge(
    variables_categorielles_ohe, left_index=True, right_index=True
)

# Réorganisation des données
X = X_global.to_numpy()
Y = np.array(data_model["CM"])

#### Fitting avec Cross-Validation

**Exercice :** construisez un modèle RF (RandomForestRegressor) en implémentant la technique de validation croisée. Pensez à enregistrer au sein d'une variable/liste les performances (MAE, MSE & RMSE) du modèle au sein de chaque fold.

In [24]:
# Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Random Forest regressor
rf_regressor = RandomForestRegressor(n_estimators=100, random_state=42)

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

In [25]:
# Entrainement avec cross-validation
for train_index, test_index in kf.split(X):
    X_train, X_test = X[train_index], X[test_index]
    y_train, y_test = Y[train_index], Y[test_index]

    # Fitting
    rf_regressor.fit(X_train, y_train)

    # Evaluation du modèle
    y_pred_test = rf_regressor.predict(X_test)

    MAE = metrics.mean_absolute_error(y_test, y_pred_test)
    MSE = metrics.mean_squared_error(y_test, y_pred_test)
    RMSE = metrics.root_mean_squared_error(y_test, y_pred_test)

    # Concaténation des résultats
    MAE_scores.append(MAE)
    MSE_scores.append(MSE)
    RMSE_scores.append(RMSE)

In [26]:
# Métriques sur tous les folds

# MAE
for fold, mae in enumerate(MAE_scores, start=1):
    print(f"Fold {fold} MAE:", mae)

Fold 1 MAE: 4007.8326951515155
Fold 2 MAE: 3651.8632978787878
Fold 3 MAE: 4718.226707878788
Fold 4 MAE: 4031.310562727273
Fold 5 MAE: 4410.05992957317


In [27]:
# MSE
for fold, mse in enumerate(MSE_scores, start=1):
    print(f"Fold {fold} MSE:", mse)

Fold 1 MSE: 32761893.668576293
Fold 2 MSE: 50894497.0512714
Fold 3 MSE: 106861487.03512044
Fold 4 MSE: 35487273.569623545
Fold 5 MSE: 54729524.04672807


In [28]:
# RMSE
for fold, rmse in enumerate(RMSE_scores, start=1):
    print(f"Fold {fold} RMSE:", rmse)

Fold 1 RMSE: 5723.8006314490285
Fold 2 RMSE: 7134.037920509772
Fold 3 RMSE: 10337.38298773536
Fold 4 RMSE: 5957.119569861222
Fold 5 RMSE: 7397.940527385177


**Question :** Commentez les résultats.

### Ajout d'un Grid Search pour les hyper paramètres

#### Sampling

In [29]:
X_global = vars_numeriques_scaled.merge(
    variables_categorielles_ohe, left_index=True, right_index=True
)
# Réorganisation des données
X = X_global.to_numpy()
Y = np.array(data_model["CM"])

#### Fitting avec Cross-Validation et *Grid Search*

**Exercice :** Intégrez la technique de Grid Search pour rechercher les paramètres optimaux du modèle.

In [30]:
# Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

# Hyperparamètres à tester
n_estimators_values = [60, 65, 70, 75]
max_depth_values = [None, 1, 2, 3]
min_samples_split_values = [5, 8, 10, 11, 13, 14, 15]

# Liste pour sauveagrder les meilleurs résultats
best_score = np.inf
best_params = {}

MAE_best_score = []
MSE_best_score = []
RMSE_best_score = []

In [31]:
# grid search à la main
for n_estimators in n_estimators_values:
    for max_depth in max_depth_values:
        for min_samples_split in min_samples_split_values:
            # Réinitialisation des résultats
            MAE_scores = []
            MSE_scores = []
            RMSE_scores = []

            # Boucle de Cross-Validation
            for train_index, test_index in kf.split(X):
                X_train, X_test = X[train_index], X[test_index]
                y_train, y_test = Y[train_index], Y[test_index]

                # Modèle avec hyperparamètres actuels
                rf_regressor = RandomForestRegressor(
                    n_estimators=n_estimators,
                    max_depth=max_depth,
                    min_samples_split=min_samples_split,
                    random_state=42,
                )

                rf_regressor.fit(X_train, y_train)

                # Evaluation du modèle
                y_pred_test = rf_regressor.predict(X_test)

                MAE = metrics.mean_absolute_error(y_test, y_pred_test)
                MSE = metrics.mean_squared_error(y_test, y_pred_test)
                RMSE = metrics.root_mean_squared_error(y_test, y_pred_test)

                # Concaténation des résultats
                MAE_scores.append(MAE)
                MSE_scores.append(MSE)
                RMSE_scores.append(RMSE)

            # Calcul du meilleur score pour le jeu de paramètres
            min_rmse = np.min(RMSE_scores)

            # Mise à jour du meilleur score si besoin
            if min_rmse < best_score:
                best_score = min_rmse
                best_params = {
                    "n_estimators": n_estimators,
                    "max_depth": max_depth,
                    "min_samples_split": min_samples_split,
                }

                # Sauvegarde des scores pour analyse
                MAE_best_score = MAE_scores
                MSE_best_score = MSE_scores
                RMSE_best_score = RMSE_scores

                # Sauvegarde du modèle pour l'utiliser directement
                best_model_regressor = rf_regressor

In [32]:
# Meilleurs résultats
print("Meilleurs paramètres:", best_params)
print("Meilleure RMSE :", best_score)

Meilleurs paramètres: {'n_estimators': 65, 'max_depth': 1, 'min_samples_split': 5}
Meilleure RMSE : 4548.156488811854


In [33]:
# Métriques sur tous les folds

# RMSE
for fold, rmse in enumerate(RMSE_best_score, start=1):
    print(f"Fold {fold} RMSE:", rmse)

Fold 1 RMSE: 5168.96443207593
Fold 2 RMSE: 6779.919772901815
Fold 3 RMSE: 10081.628056733409
Fold 4 RMSE: 4548.156488811854
Fold 5 RMSE: 6713.822743503048


In [34]:
# MAE
for fold, mse in enumerate(MSE_best_score, start=1):
    print(f"Fold {fold} MSE:", mse)

Fold 1 MSE: 26718193.300066035
Fold 2 MSE: 45967312.126985006
Fold 3 MSE: 101639224.27431424
Fold 4 MSE: 20685727.446721368
Fold 5 MSE: 45075415.831178784


In [35]:
# MSE
for fold, mae in enumerate(MAE_best_score, start=1):
    print(f"Fold {fold} MAE:", mae)

Fold 1 MAE: 3516.8014139306597
Fold 2 MAE: 3209.253810522964
Fold 3 MAE: 4545.1440942571835
Fold 4 MAE: 3088.226098509521
Fold 5 MAE: 3576.4647056529234


**Question :** Commentez les résultats

### Implémentation avec les librairies existantes

In [36]:
import numpy as np
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV, KFold

In [37]:
# Sampling en 80% train et 20% test
X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42
)

In [38]:
# Supposons que vous ayez des données d'entraînement X_train et y_train

# Définir la grille d'hyperparamètres à rechercher
param_grid = {
    "n_estimators": [60, 65, 70, 75],
    "max_depth": [None, 1, 2, 3],
    "min_samples_split": [5, 8, 10, 11, 13, 14, 15],
}
# Nombre de folds pour la validation croisée
num_folds = 5

In [39]:
# Initialisation du modèle RandomForestRegressor
rf = RandomForestRegressor(random_state=42)

# Création de l'objet GridSearchCV pour la recherche sur grille avec validation croisée
grid_search = GridSearchCV(
    estimator=rf,
    param_grid=param_grid,
    cv=KFold(
        n_splits=num_folds, shuffle=True, random_state=42
    ),  # Validation croisée avec 5 folds
    scoring="neg_mean_squared_error",  # Métrique d'évaluation (moins c'est mieux)
    n_jobs=-1,  # Utiliser tous les cœurs du processeur
)

# Exécution de la recherche sur grille
grid_search.fit(X_train, y_train)

# Afficher les meilleurs hyperparamètres
best_params = grid_search.best_params_
print("Meilleurs hyperparamètres : ", best_params)

Meilleurs hyperparamètres :  {'max_depth': 1, 'min_samples_split': 5, 'n_estimators': 60}


In [40]:
# Initialiser le modèle final avec les meilleurs hyperparamètres
best_rf = RandomForestRegressor(random_state=42, **best_params)

In [41]:
# Cross validation
# RMSE de chaque fold
rmse_scores = cross_val_score(
    best_rf, X_train, y_train, cv=num_folds, scoring="neg_root_mean_squared_error"
)

# Afficher les scores pour chaque fold
for i, score in enumerate(rmse_scores):
    print(f"RMSE pour le fold {i + 1}: {score}")

# MSE de chaque fold
mse_scores = cross_val_score(
    best_rf, X_train, y_train, cv=num_folds, scoring="neg_mean_squared_error"
)

# Afficher les scores pour chaque fold
print("\n")
for i, score in enumerate(mse_scores):
    print(f"MSE pour le fold {i + 1}: {score}")

# MAE de chaque fold
mae_scores = cross_val_score(
    best_rf, X_train, y_train, cv=num_folds, scoring="neg_mean_absolute_error"
)

# Afficher les scores pour chaque fold
print("\n")
for i, score in enumerate(mae_scores):
    print(f"MAE pour le fold {i + 1}: {score}")

RMSE pour le fold 1: -8836.353449486982
RMSE pour le fold 2: -5242.128416843558
RMSE pour le fold 3: -7205.432382938018
RMSE pour le fold 4: -4902.177844748944
RMSE pour le fold 5: -7707.687751500834


MSE pour le fold 1: -78081142.28426048
MSE pour le fold 2: -27479910.338678744
MSE pour le fold 3: -51918255.825091854
MSE pour le fold 4: -24031347.6215474
MSE pour le fold 5: -59408450.47463598


MAE pour le fold 1: -4047.520107345083
MAE pour le fold 2: -3389.6166968886077
MAE pour le fold 3: -3373.620497619359
MAE pour le fold 4: -3186.2100657449696
MAE pour le fold 5: -4145.078817961569


In [42]:
# Entraîner le modèle final sur toute la base
best_rf.fit(X_train, y_train)

# Faire des prédictions sur l'ensemble de test
y_pred = best_rf.predict(X_test)

In [43]:
# Calculer la métrique de performance (dans ce cas, RMSE)
rmse = metrics.root_mean_squared_error(y_test, y_pred)
print(f"RMSE : {rmse}")

# Calculer la métrique de performance (dans ce cas, MSE)
mse = metrics.mean_squared_error(y_test, y_pred)
print(f"MSE : {mse}")

# Calculer la métrique de performance (dans ce cas, MAE)
mae = metrics.mean_absolute_error(y_test, y_pred)
print(f"MAE : {mae}")

RMSE : 6792.775060864194
MSE : 46141793.02749855
MAE : 3387.6746891178996
